In [2]:
url = "https://github.com/booluckgmie/sharecode/raw/refs/heads/master/SARA2025/merchants_sara30072025.csv"

import pandas as pd
df = pd.read_csv(url)
df.head()

Store  \
0                              PERNIAGAAN NAZILI   
1                    PASARAYA ECONO BATU LINTANG   
2                SING KWONG SUPERMARKET (BATU 8)   
3  99 SPEEDMART SDN BHD (TMN MEGAH RIA 2) - 3015   
4           PASARAYA MILLENNIUM (MANTIN) SDN BHD   

                                             Address            state  
0  LOT 246, KAMPUNG MERKANG 16800 PASIR PUTEH KEL...         KELANTAN  
1  LOT 27397B, KAMPUNG BUKIT SUNGAI PASIR 08000 S...            KEDAH  
2  SUBLOT 61-63 OF LOT 341, BLOCK 33 AND LOT 1337...          SARAWAK  
3  NO : 27 & 29 (GROUND FLOOR), JALAN KEMPAS 17 T...            JOHOR  
4  5G,7G,9G,11G JALAN BESAR MANTIN 71700 MANTIN N...  NEGERI SEMBILAN

In [4]:
import pandas as pd
import time
from tqdm import tqdm
import folium
from geopy.geocoders import Nominatim
from geopy.exc import GeocoderQueryError, GeocoderInsufficientPrivileges
from tenacity import retry, stop_after_attempt, wait_fixed

# Load dataset
data = df.copy()

# Fix the column name typo
data['address'] = data['Store'] + ", " + data['Address'] + ", MALAYSIA"
# data['address'] = data['address'].str.replace(r"[()]", "", regex=True)

# Initialize geolocator with a unique user agent
geolocator = Nominatim(user_agent="my_geocoder_script")

# Define the geocode_with_retry function with retry logic
@retry(stop=stop_after_attempt(3), wait=wait_fixed(2))
def geocode_with_retry(address):
    try:
        return geolocator.geocode(address, timeout=10)
    except GeocoderQueryError as e:
        print(f"GeocoderQueryError: {e}")
        return None
    except GeocoderInsufficientPrivileges:
        print("Blocked by Geocoder. Reduce request rate or switch API.")
        return None

# Add a progress bar using tqdm
tqdm.pandas()

# Function to apply geocoding with rate limiting
def apply_geocode_with_retry(x):
    if pd.notnull(x):
        try:
            time.sleep(1.5)  # Add delay to avoid rate limiting
            return geocode_with_retry(x)
        except Exception as e:
            print(f"Error processing address: {x}, Error: {e}")
            return None
    return None

# Apply function to address column
data['geocoded'] = data['address'].progress_apply(apply_geocode_with_retry)

# Extract latitude and longitude safely
data['latitude'] = data['geocoded'].apply(lambda x: x.latitude if x else None)
data['longitude'] = data['geocoded'].apply(lambda x: x.longitude if x else None)

# Display DataFrame
# print(data[['Address', 'latitude', 'longitude']])


100%|██████████| 3916/3916 [2:15:02<00:00,  2.07s/it]  


In [5]:
data.to_csv('saraMerchants31072025_geocoded.csv', index=False)

## geocode by zumaidi

In [12]:
data = pd.read_csv('sara2025_geocoded.csv')

In [13]:
data.head()

Store  \
0   NAHMEE TRADING (M) SDN BHD - GEDONG   
1  NAHMEE TRADING (M) SDN BHD - MELIKIN   
2                JIT SIANG (LUBOK ANTU)   
3            LIK SENG MARKETING SDN BHD   
4                        TAN KIANG SENG   

                                             Address    State  Latitude  \
0  SL-1-4, LOT 399-402 BLOCK 18, MELIKIN LAND DIS...  SARAWAK  1.033333   
1  SL-1-4, LOT 399-402 BLOCK 18, MELIKIN LAND DIS...  SARAWAK  1.033333   
2  NO 47&48 PEKAN LUBOK ANTU 95900 LUBOK ANTU SAR...  SARAWAK  1.042934   
3  LOT 167, LUBOK ANTU BAZAAR, LUBOK ANTU, 95900 ...  SARAWAK  1.042934   
4  NO. 11 LUBOK ANTU BAZAAR 95900 LUBOK ANTU SARAWAK  SARAWAK  1.042934   

    Longitude  
0  110.766667  
1  110.766667  
2  111.832838  
3  111.832838  
4  111.832838

In [23]:
import folium
from folium.plugins import MarkerCluster
from branca.element import Template, MacroElement
import json

data2 = data.dropna()

map_center = [data2['Latitude'].mean(), data2['Longitude'].mean()]
m = folium.Map(location=map_center, zoom_start=5, tiles='CartoDB positron')

# Create marker cluster with a specific name
marker_cluster = MarkerCluster(name='store_cluster').add_to(m)

# Store marker information for search
markers_info = []
created_markers = []

for idx, row in data2.iterrows():
    marker = folium.Marker(
        location=[row['Latitude'], row['Longitude']],
        popup=folium.Popup(f"<b>{row['Store']}</b><br>{row['Address']}", max_width=300),
        tooltip=row['Store'],
        icon=folium.Icon(color='blue', icon='info-sign')
    )
    marker.add_to(marker_cluster)
    
    # Store both marker and its data with matching index
    created_markers.append(marker)
    markers_info.append({
        'store': str(row['Store']),
        'address': str(row['Address']),
        'lat': float(row['Latitude']),
        'lng': float(row['Longitude']),
        'tooltip': str(row['Store'])  # Add tooltip for matching
    })

folium.LayerControl().add_to(m)

# Create the search functionality
search_html = f"""
{{% macro html(this, kwargs) %}}
<style>
    #search-container {{
        position: fixed;
        top: 10px;
        left: 50%;
        transform: translateX(-50%);
        z-index: 9999;
        background-color: white;
        padding: 10px;
        border-radius: 8px;
        box-shadow: 0 2px 10px rgba(0,0,0,0.3);
        font-family: Arial, sans-serif;
    }}
    #search-input {{
        width: 280px;
        padding: 8px 12px;
        border: 2px solid #ddd;
        border-radius: 4px;
        font-size: 14px;
    }}
    #search-button {{
        padding: 8px 15px;
        background-color: #007bff;
        color: white;
        border: none;
        border-radius: 4px;
        cursor: pointer;
        margin-left: 5px;
    }}
    #search-button:hover {{
        background-color: #0056b3;
    }}
    #clear-button {{
        padding: 8px 15px;
        background-color: #6c757d;
        color: white;
        border: none;
        border-radius: 4px;
        cursor: pointer;
        margin-left: 5px;
    }}
    #clear-button:hover {{
        background-color: #545b62;
    }}
    #search-results {{
        position: fixed;
        top: 70px;
        left: 50%;
        transform: translateX(-50%);
        z-index: 9998;
        background-color: white;
        border-radius: 4px;
        box-shadow: 0 2px 10px rgba(0,0,0,0.3);
        max-height: 300px;
        overflow-y: auto;
        display: none;
        width: 350px;
        border: 1px solid #ddd;
    }}
    .result-item {{
        padding: 10px;
        cursor: pointer;
        border-bottom: 1px solid #eee;
    }}
    .result-item:hover {{
        background-color: #f8f9fa;
    }}
    .result-item:last-child {{
        border-bottom: none;
    }}
    .result-store {{
        font-weight: bold;
        color: #007bff;
    }}
    .result-address {{
        color: #666;
        font-size: 12px;
        margin-top: 2px;
    }}
    .no-results {{
        padding: 15px;
        text-align: center;
        color: #666;
    }}
</style>

<div id="search-container">
    <input type="text" id="search-input" placeholder="🔍 Search store name or address...">
    <button id="search-button">Search</button>
    <button id="clear-button">Clear</button>
</div>
<div id="search-results"></div>

<script>
    // Store all marker data
    var markersData = {json.dumps(markers_info)};
    var map;
    var markerCluster;
    var allMarkers = [];
    var isSearchActive = false;
    
    // Wait for map to fully load
    setTimeout(function() {{
        // Find the map object
        for (var key in window) {{
            if (key.startsWith('map_') && window[key]._container) {{
                map = window[key];
                break;
            }}
        }}
        
        if (!map) {{
            console.error('Map not found');
            return;
        }}
        
        // Find the marker cluster and collect markers in order
        map.eachLayer(function(layer) {{
            if (layer instanceof L.MarkerClusterGroup) {{
                markerCluster = layer;
                // Collect markers and match them with data by tooltip
                layer.eachLayer(function(marker) {{
                    var tooltipContent = '';
                    if (marker.getTooltip && marker.getTooltip()) {{
                        tooltipContent = marker.getTooltip().getContent();
                    }}
                    
                    // Find matching data entry
                    var matchIndex = -1;
                    for (var i = 0; i < markersData.length; i++) {{
                        if (markersData[i].tooltip === tooltipContent) {{
                            matchIndex = i;
                            break;
                        }}
                    }}
                    
                    if (matchIndex !== -1) {{
                        allMarkers[matchIndex] = marker;
                    }} else {{
                        allMarkers.push(marker);
                    }}
                }});
            }}
        }});
        
        console.log('Found', allMarkers.length, 'markers');
        
        // Set up event listeners
        var searchInput = document.getElementById('search-input');
        var searchButton = document.getElementById('search-button');
        var clearButton = document.getElementById('clear-button');
        var searchResults = document.getElementById('search-results');
        
        // Search function
        function performSearch() {{
            var query = searchInput.value.toLowerCase().trim();
            
            if (query === '') {{
                showAllMarkers();
                searchResults.style.display = 'none';
                return;
            }}
            
            var matches = [];
            markersData.forEach(function(data, index) {{
                if (data.store.toLowerCase().includes(query) || 
                    data.address.toLowerCase().includes(query)) {{
                    matches.push({{
                        index: index,
                        data: data
                    }});
                }}
            }});
            
            displayResults(matches);
            filterMarkers(matches);
            isSearchActive = true;
        }}
        
        // Display search results
        function displayResults(matches) {{
            var html = '';
            
            if (matches.length === 0) {{
                html = '<div class="no-results">No results found</div>';
            }} else {{
                matches.forEach(function(match) {{
                    html += '<div class="result-item" onclick="zoomToMarker(' + 
                           match.data.lat + ',' + match.data.lng + ')">' +
                           '<div class="result-store">' + match.data.store + '</div>' +
                           '<div class="result-address">' + match.data.address + '</div>' +
                           '</div>';
                }});
            }}
            
            searchResults.innerHTML = html;
            searchResults.style.display = 'block';
        }}
        
        // Filter markers based on search
        function filterMarkers(matches) {{
            if (!markerCluster) return;
            
            // Clear cluster
            markerCluster.clearLayers();
            
            // Add only matching markers
            matches.forEach(function(match) {{
                var marker = allMarkers[match.index];
                if (marker) {{
                    markerCluster.addLayer(marker);
                }}
            }});
            
            console.log('Filtered to', matches.length, 'markers');
        }}
        
        // Show all markers
        function showAllMarkers() {{
            if (!markerCluster) return;
            
            markerCluster.clearLayers();
            allMarkers.forEach(function(marker) {{
                markerCluster.addLayer(marker);
            }});
            isSearchActive = false;
        }}
        
        // Zoom to specific marker
        window.zoomToMarker = function(lat, lng) {{
            console.log('Zooming to:', lat, lng);
            map.setView([lat, lng], 16);
            searchResults.style.display = 'none';
            
            // Optional: Open popup of the marker at this location
            setTimeout(function() {{
                map.eachLayer(function(layer) {{
                    if (layer instanceof L.MarkerClusterGroup) {{
                        layer.eachLayer(function(marker) {{
                            var markerPos = marker.getLatLng();
                            if (Math.abs(markerPos.lat - lat) < 0.0001 && 
                                Math.abs(markerPos.lng - lng) < 0.0001) {{
                                marker.openPopup();
                            }}
                        }});
                    }}
                }});
            }}, 500);
        }};
        
        // Event listeners
        searchButton.addEventListener('click', performSearch);
        
        clearButton.addEventListener('click', function() {{
            searchInput.value = '';
            showAllMarkers();
            searchResults.style.display = 'none';
        }});
        
        searchInput.addEventListener('keypress', function(e) {{
            if (e.key === 'Enter') {{
                performSearch();
            }}
        }});
        
        searchInput.addEventListener('input', function() {{
            if (searchInput.value.trim() === '' && isSearchActive) {{
                showAllMarkers();
                searchResults.style.display = 'none';
            }}
        }});
        
        // Hide results when clicking outside
        document.addEventListener('click', function(e) {{
            if (!document.getElementById('search-container').contains(e.target) &&
                !document.getElementById('search-results').contains(e.target)) {{
                searchResults.style.display = 'none';
            }}
        }});
        
    }}, 2000); // Increased timeout to ensure everything is loaded
    
</script>
{{% endmacro %}}
"""

search_element = MacroElement()
search_element._template = Template(search_html)
m.get_root().add_child(search_element)

# Save the map
m.save("saraMerchants_search.html")

m